In [180]:
# initial imports
import pandas as pd
from pathlib import Path

# needed for model
from sklearn import tree
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report

# Needed for decision tree visualization
import pydotplus
from IPython.display import Image

In [182]:
csvpath = Path('../Project-03/teamGameStats.csv')
teamstats_df = pd.read_csv(csvpath)

In [183]:
teamstats_df.head(16)

TEAM      MATCHUP   GAMEDATE W/L  MIN  PTS  FGM  FGA   FG%  3PM  ...   FT%  \
0   ATL  ATL vs. IND  4/18/2021   W   48  129   45   92  48.9   13  ...  76.5   
1   CHA  CHA vs. POR  4/18/2021   W   48  109   39   83  47.0   18  ...  76.5   
2   NOP    NOP @ NYK  4/18/2021   L   53  112   41  101  40.6    6  ...  80.0   
3   MIA  MIA vs. BKN  4/18/2021   W   48  109   38   87  43.7   16  ...  81.0   
4   POR    POR @ CHA  4/18/2021   L   48  101   36   91  39.6   10  ...  67.9   
5   OKC    OKC @ TOR  4/18/2021   L   48  106   37   82  45.1   14  ...  85.7   
6   MIN    MIN @ LAC  4/18/2021   L   48  105   36   88  40.9   17  ...  76.2   
7   ORL  ORL vs. HOU  4/18/2021   L   48  110   41   91  45.1   11  ...  89.5   
8   TOR  TOR vs. OKC  4/18/2021   W   48  112   37   96  38.5   17  ...  87.5   
9   IND    IND @ ATL  4/18/2021   L   48  117   45   92  48.9   10  ...  85.0   
10  BKN    BKN @ MIA  4/18/2021   L   48  107   39   82  47.6   17  ...  66.7   
11  DAL  DAL vs. SAC  4/18/2021   L   48  107   39   87  44.8   16  ...  65.0   
12  SAC    SAC @ DAL  4/18/2021   W   48  121   44   89  49.4   11  ...  88.0   
13  LAC  LAC vs. MIN  4/18/2021   W   48  124   45   89  50.6   21  ...  76.5   
14  HOU    HOU @ ORL  4/18/2021   W   48  114   42   82  51.2   16  ...  70.0   
15  NYK  NYK vs. NOP  4/18/2021   W   53  122   45   95  47.4   11  ...  87.5   

    OREB  DREB  REB  AST  TOV  STL  BLK  PF  +/-  
0     14    37   51   20   10    8    7  19   12  
1      7    39   46   26   14    6    8  25    8  
2     20    32   52   25   13    6    4  16  -10  
3     16    37   53   28   17    9    1  13    2  
4     13    34   47   18    9    7    3  17   -8  
5      9    37   46   22   23    6    8  19   -6  
6      6    31   37   27   11    6    7  21  -19  
7      9    27   36   28   15   10    5  19   -4  
8     16    31   47   23   15    9    5  15    6  
9      8    33   41   33   12    7    5  27  -12  
10     8    30   38   26   11   10    6  17   -2  
11    10    32   42   15   14    3    8  20  -14  
12    10    32   42   22    8   11    3  19   14  
13     8    40   48   31   15    6    3  26   19  
14    10    33   43   26   19    7    7  21    4  
15    13    36   49   27   13    9    6  26   10  

[16 rows x 24 columns]

In [184]:
teamstats_df = teamstats_df.drop(columns=['TEAM','MATCHUP','GAMEDATE','+/-','PTS'])

In [185]:
teamstats_df.info('include=all')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13658 entries, 0 to 13657
Data columns (total 19 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   W/L     13658 non-null  object 
 1   MIN     13658 non-null  int64  
 2   FGM     13658 non-null  int64  
 3   FGA     13658 non-null  int64  
 4   FG%     13658 non-null  float64
 5   3PM     13658 non-null  int64  
 6   3PA     13658 non-null  int64  
 7   3P%     13658 non-null  float64
 8   FTM     13658 non-null  int64  
 9   FTA     13658 non-null  int64  
 10  FT%     13658 non-null  float64
 11  OREB    13658 non-null  int64  
 12  DREB    13658 non-null  int64  
 13  REB     13658 non-null  int64  
 14  AST     13658 non-null  int64  
 15  TOV     13658 non-null  int64  
 16  STL     13658 non-null  int64  
 17  BLK     13658 non-null  int64  
 18  PF      13658 non-null  int64  
dtypes: float64(3), int64(15), object(1)
memory usage: 2.0+ MB


In [187]:
# defining 'W/L' column as feature set
X = teamstats_df.copy()
X.drop('W/L', axis=1, inplace=True)
X.head(20)

MIN  FGM  FGA   FG%  3PM  3PA   3P%  FTM  FTA    FT%  OREB  DREB  REB  \
0    48   45   92  48.9   13   32  40.6   26   34   76.5    14    37   51   
1    48   39   83  47.0   18   43  41.9   13   17   76.5     7    39   46   
2    53   41  101  40.6    6   27  22.2   24   30   80.0    20    32   52   
3    48   38   87  43.7   16   39  41.0   17   21   81.0    16    37   53   
4    48   36   91  39.6   10   36  27.8   19   28   67.9    13    34   47   
5    48   37   82  45.1   14   33  42.4   18   21   85.7     9    37   46   
6    48   36   88  40.9   17   45  37.8   16   21   76.2     6    31   37   
7    48   41   91  45.1   11   32  34.4   17   19   89.5     9    27   36   
8    48   37   96  38.5   17   38  44.7   21   24   87.5    16    31   47   
9    48   45   92  48.9   10   32  31.3   17   20   85.0     8    33   41   
10   48   39   82  47.6   17   43  39.5   12   18   66.7     8    30   38   
11   48   39   87  44.8   16   48  33.3   13   20   65.0    10    32   42   
12   48   44   89  49.4   11   24  45.8   22   25   88.0    10    32   42   
13   48   45   89  50.6   21   42  50.0   13   17   76.5     8    40   48   
14   48   42   82  51.2   16   34  47.1   14   20   70.0    10    33   43   
15   53   45   95  47.4   11   29  37.9   21   24   87.5    13    36   49   
16   48   45   89  50.6   12   29  41.4    9   12   75.0     5    41   46   
17   48   39   91  42.9   16   47  34.0   21   27   77.8    13    32   45   
18   53   42  101  41.6   23   59  39.0    8    8  100.0     6    31   37   
19   48   39   88  44.3   12   30  40.0    6    7   85.7    11    33   44   

    AST  TOV  STL  BLK  PF  
0    20   10    8    7  19  
1    26   14    6    8  25  
2    25   13    6    4  16  
3    28   17    9    1  13  
4    18    9    7    3  17  
5    22   23    6    8  19  
6    27   11    6    7  21  
7    28   15   10    5  19  
8    23   15    9    5  15  
9    33   12    7    5  27  
10   26   11   10    6  17  
11   15   14    3    8  20  
12   22    8   11    3  19  
13   31   15    6    3  26  
14   26   19    7    7  21  
15   27   13    9    6  26  
16   23   13   10    9  17  
17   27   16    7    1   8  
18   31   16   10    3  21  
19   27   11    6    1  10

In [188]:
# defining target vector
y=teamstats_df['W/L'].values.reshape(-1,1)

In [189]:
# converting 'W/L' to 0/1's
y=teamstats_df['W/L'].apply(lambda x: 1 if x=="W" else 0)
y[:10]

0    1
1    1
2    0
3    1
4    0
5    0
6    0
7    0
8    1
9    0
Name: W/L, dtype: int64

In [190]:
# splitting data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=78)

In [191]:
X_train.shape


(10243, 18)

In [192]:
X_test.shape

(3415, 18)

In [193]:
y_train.shape

(10243,)

In [194]:
y_test.shape

(3415,)

In [195]:
# creating the decision tree classifier instance
model = tree.DecisionTreeClassifier()

In [196]:
# fitting the model
model = model.fit(X_train, y_train)

In [197]:
# predictions using the testing data
predictions = model.predict(X_test)

In [198]:
cm = confusion_matrix(y_test, predictions)
cm_df = pd.DataFrame(
cm, index=['Actual 0', 'Actual 1'], columns=['Predicted 0', 'Predicted 1'])

acc_score = accuracy_score(y_test, predictions)

In [199]:
# Displaying results
print("Confusion Matrix")
display(cm_df)
print(f"Accuracy Score : {acc_score}")
print("Classification Report")
print(classification_report(y_test, predictions))

Confusion Matrix


Predicted 0  Predicted 1
Actual 0         1227          477
Actual 1          460         1251

Accuracy Score : 0.7256222547584188
Classification Report
              precision    recall  f1-score   support

           0       0.73      0.72      0.72      1704
           1       0.72      0.73      0.73      1711

    accuracy                           0.73      3415
   macro avg       0.73      0.73      0.73      3415
weighted avg       0.73      0.73      0.73      3415



In [200]:
# Create DOT data
dot_data = tree.export_graphviz(
    model, out_file=None, feature_names=X.columns, class_names=["0", "1"], filled=True
)

# Draw graph
graph = pydotplus.graph_from_dot_data(dot_data)

# Show graph
Image(graph.create_png())

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.451131 to fit

